# 🌱 NDVI Classification with LightGBM & Pseudo-Labeling
Welcome! In this notebook, we'll build a high-accuracy classifier for NDVI data using LightGBM and pseudo-labeling. Each step is explained for beginners, with tips and feature importance analysis!

<div style="text-align: center;">
    <img src="https://upload.wikimedia.org/wikipedia/commons/f/fa/Breathing_planet_-_vegetation_-_GIF_%2850906243727%29.gif" width="300" alt="NDVI Example"/>
</div>

## 1. Importing Libraries
Let's start by importing the essential Python libraries for data science and machine learning. We'll also suppress warnings for a cleaner output.

In [1]:
import pandas as pd
import numpy as np
from sklearn.model_selection import StratifiedKFold
from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import accuracy_score
from lightgbm import LGBMClassifier
import warnings

# Suppress warnings
warnings.filterwarnings('ignore', category=UserWarning)

## 2. Loading the Data
We'll load the training and test datasets, and drop any unnecessary columns. Always check your data after loading!

In [ ]:
train = pd.read_csv('Dataset/hacktrain.csv')
test = pd.read_csv('Dataset/hacktest.csv')
train.drop(columns=['Unnamed: 0'], inplace=True, errors='ignore')
test.drop(columns=['Unnamed: 0'], inplace=True, errors='ignore')
train.head()

/usr/local/lib/python3.11/dist-packages/pandas/io/formats/format.py:1458: RuntimeWarning: invalid value encountered in greater
  has_large_values = (abs_vals > 1e6).any()
/usr/local/lib/python3.11/dist-packages/pandas/io/formats/format.py:1459: RuntimeWarning: invalid value encountered in less
  has_small_values = ((abs_vals < 10 ** (-self.digits)) & (abs_vals > 0)).any()
/usr/local/lib/python3.11/dist-packages/pandas/io/formats/format.py:1459: RuntimeWarning: invalid value encountered in greater
  has_small_values = ((abs_vals < 10 ** (-self.digits)) & (abs_vals > 0)).any()
/usr/local/lib/python3.11/dist-packages/pandas/io/formats/format.py:1458: RuntimeWarning: invalid value encountered in greater
  has_large_values = (abs_vals > 1e6).any()
/usr/local/lib/python3.11/dist-packages/pandas/io/formats/format.py:1459: RuntimeWarning: invalid value encountered in less
  has_small_values = ((abs_vals < 10 ** (-self.digits)) & (abs_vals > 0)).any()
/usr/local/lib/python3.11/dist-packages/pan

ID  class  20150720_N  20150602_N  20150517_N  20150501_N  20150415_N  \
0   1  water    637.5950     658.668   -1882.030    -1924.36     997.904   
1   2  water    634.2400     593.705   -1625.790    -1672.32     914.198   
2   4  water     58.0174   -1599.160         NaN    -1052.63         NaN   
3   5  water     72.5180         NaN     380.436    -1256.93     515.805   
4   8  water   1136.4400         NaN         NaN     1647.83    1935.800   

   20150330_N  20150314_N  20150226_N  ...  20140610_N  20140525_N  \
0   -1739.990     630.087         NaN  ...         NaN   -1043.160   
1    -692.386     707.626   -1670.590  ...         NaN    -933.934   
2   -1564.630         NaN     729.790  ...    -1025.88     368.622   
3   -1413.180    -802.942     683.254  ...    -1813.95     155.624   
4         NaN    2158.980         NaN  ...     1535.00    1959.430   

   20140509_N  20140423_N  20140407_N  20140322_N  20140218_N  20140202_N  \
0   -1942.490     267.138         NaN         NaN     211.328   -2203.020   
1    -625.385     120.059     364.858     476.972     220.878   -2250.000   
2         NaN   -1227.800     304.621         NaN     369.214   -2202.120   
3         NaN    -924.073     432.150     282.833     298.320   -2197.360   
4    -279.317    -384.915    -113.406    1020.720    1660.650    -116.801   

   20140117_N  20140101_N  
0    -1180.19     433.906  
1    -1360.56     524.075  
2         NaN   -1343.550  
3         NaN    -826.727  
4     -568.05   -1357.140  

[5 rows x 29 columns]

## 3. Identifying NDVI Columns
NDVI stands for Normalized Difference Vegetation Index—a key indicator in remote sensing! Let's find all columns related to NDVI.

In [3]:
ndvi_columns = [col for col in train.columns if '_N' in col]
print(f"NDVI columns: {ndvi_columns[:5]} ... total: {len(ndvi_columns)}")

NDVI columns: ['20150720_N', '20150602_N', '20150517_N', '20150501_N', '20150415_N'] ... total: 27


## 4. Filling Missing NDVI Values
We'll fill missing NDVI values using interpolation and mean imputation. This helps the model learn better!

In [4]:
def fill_missing(df, columns):
    df[columns] = df[columns].interpolate(axis=1, limit_direction='both')
    df[columns] = df[columns].fillna(df[columns].mean())
    return df

train = fill_missing(train, ndvi_columns)
test = fill_missing(test, ndvi_columns)
train[ndvi_columns].isnull().sum().sum()

0

## 5. Feature Engineering
Let's create new features from NDVI columns, including statistics, trends, differences, and rolling statistics.

In [5]:
def create_features(df, columns):
    # Basic statistics
    df['ndvi_mean'] = df[columns].mean(axis=1)
    df['ndvi_std'] = df[columns].std(axis=1)
    df['ndvi_min'] = df[columns].min(axis=1)
    df['ndvi_max'] = df[columns].max(axis=1)
    
    # Trends and differences
    df['ndvi_trend'] = df[columns].apply(lambda x: np.polyfit(range(len(x)), x, 1)[0], axis=1)
    for i in range(1, len(columns)):
        df[f'ndvi_diff_{i}'] = df[columns[i]] - df[columns[i-1]]
    
    # Rolling statistics (fixed implementation)
    for window in [3, 5]:
        rolling_mean = df[columns].T.rolling(window=window).mean().T
        rolling_std = df[columns].T.rolling(window=window).std().T
        df[f'ndvi_rolling_mean_{window}'] = rolling_mean.iloc[:, -1]
        df[f'ndvi_rolling_std_{window}'] = rolling_std.iloc[:, -1]
    
    return df

train = create_features(train, ndvi_columns)
test = create_features(test, ndvi_columns)
train[['ndvi_mean', 'ndvi_std', 'ndvi_trend', 'ndvi_rolling_mean_3', 'ndvi_rolling_std_3']].head()

ndvi_mean     ndvi_std  ndvi_trend  ndvi_rolling_mean_3  \
0 -269.881519  1017.144905   -1.812555          -983.101333   
1 -248.218496   935.550461    0.410666         -1028.828333   
2 -631.649152  1045.094565    8.399337         -1772.835000   
3 -319.884926  1024.098285  -16.228253         -1512.043500   
4  767.647759  1209.705801  -61.719074          -680.663667   

   ndvi_rolling_std_3  
0         1329.465170  
1         1416.477127  
2          429.285000  
3          685.316500  
4          627.791038

## 6. Preparing Features and Target
We'll select all feature columns and encode the target variable for classification.

In [6]:
feature_columns = [col for col in train.columns if col not in ['ID', 'class']]
le = LabelEncoder()
y = le.fit_transform(train['class'])
X = train[feature_columns].copy()
X_test = test[feature_columns].copy()
print(f"Classes: {le.classes_}")

Classes: ['farm' 'forest' 'grass' 'impervious' 'orchard' 'water']


## 7. Cross-Validation with LightGBM
We'll use 5-fold Stratified Cross-Validation to train and validate our model. This helps prevent overfitting and gives a reliable accuracy estimate.

In [7]:
oof_preds = np.zeros((X.shape[0], len(le.classes_)))
test_preds = np.zeros((X_test.shape[0], len(le.classes_)))

skf = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)

for fold, (train_idx, val_idx) in enumerate(skf.split(X, y)):
    print(f"\nFold {fold+1}")
    X_train, X_val = X.iloc[train_idx], X.iloc[val_idx]
    y_train, y_val = y[train_idx], y[val_idx]

    # Define LightGBM model with correct parameters
    clf = LGBMClassifier(
        n_estimators=1000,
        learning_rate=0.05,
        num_leaves=63,
        max_depth=-1,
        min_child_samples=20,
        reg_alpha=0.1,
        reg_lambda=0.1,
        colsample_bytree=0.8,
        subsample=0.8,
        objective='multiclass',
        class_weight='balanced',
        random_state=42,
        n_jobs=-1,
        verbose=100
    )
    
    # Fit without eval_set and early_stopping for simplicity
    clf.fit(X_train, y_train)

    # Store predictions
    oof_preds[val_idx] = clf.predict_proba(X_val)
    test_preds += clf.predict_proba(X_test) / skf.n_splits

    # Evaluate fold accuracy
    fold_accuracy = accuracy_score(y_val, np.argmax(oof_preds[val_idx], axis=1))
    print(f"Fold {fold+1} Accuracy: {fold_accuracy:.4f}")

# Compute and display OOF accuracy
oof_accuracy = accuracy_score(y, np.argmax(oof_preds, axis=1))
print(f"\n✅ OOF Accuracy: {oof_accuracy:.4f}")


Fold 1
[LightGBM] [Debug] Dataset::GetMultiBinFromAllFeatures: sparse rate 0.002397
[LightGBM] [Debug] init for col-wise cost 0.000974 seconds, init for row-wise cost 0.004995 seconds
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.007455 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 15810
[LightGBM] [Info] Number of data points in the train set: 6400, number of used features: 62
[LightGBM] [Info] Start training from score -1.791759
[LightGBM] [Info] Start training from score -1.791759
[LightGBM] [Info] Start training from score -1.791759
[LightGBM] [Info] Start training from score -1.791759
[LightGBM] [Info] Start training from score -1.791760
[LightGBM] [Info] Start training from score -1.791759
[LightGBM] [Debug] Trained a tree with leaves = 63 and depth = 12
[LightGBM] [Debug] Trained a tree with leaves = 63 and depth = 12
[LightGBM] [Warning] No further splits with positive gain, best gain: 

## 8. Pseudo-Labeling with Confidence Threshold
We'll use test predictions with high confidence (≥ 0.99) as extra training data for a final model.

In [8]:
super_conf_idx = np.where(test_preds.max(axis=1) >= 0.99)[0]
X_pseudo = X_test.iloc[super_conf_idx]
y_pseudo = np.argmax(test_preds[super_conf_idx], axis=1)

print(f"\nPseudo-labeled samples added: {len(y_pseudo)}/{len(X_test)}")


Pseudo-labeled samples added: 2111/2845


## 9. Combine Training Data with Pseudo-Labels
Let's combine the original training data with the pseudo-labeled samples for a stronger final model.

In [9]:
if len(y_pseudo) > 0:
    X_final = pd.concat([X, X_pseudo], axis=0)
    y_final = np.concatenate([y, y_pseudo])
else:
    X_final = X.copy()
    y_final = y.copy()

## 10. Train Final Model on Combined Data
We'll train a final LightGBM model using all available data.

In [10]:
final_clf = LGBMClassifier(
    n_estimators=1500,
    learning_rate=0.02,
    num_leaves=127,
    max_depth=-1,
    min_child_samples=15,
    random_state=42,
    verbose=-1
)

final_clf.fit(X_final, y_final)

LGBMClassifier(learning_rate=0.02, min_child_samples=15, n_estimators=1500,
               num_leaves=127, random_state=42, verbose=-1)

## 11. Evaluate Final Model & Feature Importance
Let's check the final model's accuracy and see which features are most important.

In [11]:
final_preds_train = final_clf.predict(X)
final_accuracy = accuracy_score(y, final_preds_train)
print(f"\n✅ Final Training Accuracy: {final_accuracy:.4f}")

# Feature importance
fi = pd.DataFrame({
    'feature': feature_columns,
    'importance': final_clf.feature_importances_
}).sort_values('importance', ascending=False)

print("\nTop 10 Features:")
print(fi.head(10))


✅ Final Training Accuracy: 1.0000

Top 10 Features:
         feature  importance
30      ndvi_max       13851
28      ndvi_std       13218
29      ndvi_min       10228
45  ndvi_diff_14        8616
15    20140813_N        8498
19    20140509_N        8186
46  ndvi_diff_15        7522
13    20141016_N        7491
14    20140930_N        6854
26    20140101_N        6051


## 12. Make Predictions & Save Submission
We'll predict the classes for the test set and save the results for submission.

In [12]:
final_preds_test = final_clf.predict(X_test)
final_labels = le.inverse_transform(final_preds_test)

submission = pd.DataFrame({
    'ID': test['ID'],
    'class': final_labels
})
submission.to_csv('submission.csv', index=False)
print("\n✅ submission.csv saved!")
submission.head()


✅ submission.csv saved!


ID   class
0   1    farm
1   2  forest
2   3  forest
3   4    farm
4   5  forest

---
🎉 **Congratulations!**  
You've built a high-accuracy NDVI classifier using LightGBM and advanced feature engineering.  
Try experimenting with different models or feature engineering for even better results!

<img src="https://www.kaggle.com/static/images/site-logo.png" width="120" alt="Kaggle Logo"/>